In [1]:
import os
import json
import numpy as np
import pandas as pd
import altair as alt

In [2]:
__author__ = 'Aleksandar Anžel'
__copyright__ = ''
__credits__ = ['Aleksandar Anžel']
__license__ = 'GNU General Public License v3.0'
__version__ = '1.0'
__maintainer__ = 'Aleksandar Anžel'
__email__ = 'aleksandar.anzel@uni-marburg.de'
__status__ = 'Dev'

In [3]:
# Uncomment if you are using dark jupyter lab/notebook theme
alt.renderers.set_embed_options(theme='dark')
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

# 0. Define paths

In [4]:
path_root_data = os.path.join('..', 'Data')
path_cmangoes_vis_data = os.path.join(
    path_root_data, 'Visualization_data', 'data', 'multiple_datasets', 'vis',
    'mds_1_Overview')
path_peptidereactor_vis_data = os.path.join(
    path_root_data, 'Visualization_data', 'peptidereactor_vis_data')

path_peptidereactor_vega_lite_spec = os.path.join(
    path_cmangoes_vis_data, 'mds_1_Overview.json')

path_cmangoes_source_data = os.path.join(
    path_cmangoes_vis_data, 'hm_source_data.json')
path_cmangoes_imb_data = os.path.join(
    path_cmangoes_vis_data, 'hm_imb_data.json')
path_cmangoes_bio_data = os.path.join(
    path_cmangoes_vis_data, 'hm_bio_data.json')

path_peptidereactor_source_data = os.path.join(
    path_peptidereactor_vis_data, 'hm_source_data.json')
path_peptidereactor_imb_data = os.path.join(
    path_peptidereactor_vis_data, 'hm_imb_data.json')
path_peptidereactor_bio_data = os.path.join(
    path_peptidereactor_vis_data, 'hm_bio_data.json')

list_of_datasets = [
    'ace_vaxinpad',
    'acp_anticp',
    'acp_iacp',
    'acp_mlacp',
    'afp_amppred',
    'afp_antifp',
    'aip_aippred',
    'aip_antiinflam',
    'amp_antibp',
    'amp_antibp2',
    'amp_csamp',
    'amp_fernandes',
    'amp_gonzales',
    'amp_iamp2l',
    'amp_modlamp',
    'atb_antitbp',
    'atb_iantitb',
    'avp_amppred',
    'avp_avppred',
    'bce_ibce',
    'cpp_cellppd',
    'cpp_cellppdmod',
    'cpp_cppredfl',
    'cpp_kelmcpp',
    'cpp_mixed',
    'cpp_mlcpp',
    'cpp_mlcppue',
    'cpp_sanders',
    'hem_hemopi'
]

# 1. Import data

In [5]:
df_cmangoes_source_data = pd.read_json(path_cmangoes_source_data)
df_cmangoes_imb_data = pd.read_json(path_cmangoes_imb_data)
df_cmangoes_bio_data = pd.read_json(path_cmangoes_bio_data)
df_peptidereactor_source_data = pd.read_json(path_peptidereactor_source_data)
df_peptidereactor_imb_data = pd.read_json(path_peptidereactor_imb_data)
df_peptidereactor_bio_data = pd.read_json(path_peptidereactor_bio_data)

# 2. Clean the data

In [6]:
def df_clean_cmangoes_data(df_input):
    df_output = df_input.copy(deep=True)
    
    df_output.drop(
        df_output[df_output['Encoding'].str.startswith('str')].index,
        inplace=True)
    
    df_output['Encoding_max'] = df_output[
        'Encoding_max'].str.replace('_levels_1_and_2_encoding','')
    df_output['Encoding_max'] = df_output[
        'Encoding_max'].str.replace('seq','CMANGOES_seq_')
    df_output['Encoding'] = df_output[
        'Encoding'].str.replace('seq','param_seq_')
    
    return df_output.reset_index(drop=True)
    

In [7]:
df_cmangoes_source_data

Dataset Encoding                                    Encoding_max  \
0    amp_gonzales   seqdis  seqdiscretized_shifted_levels_1_and_2_encoding   
1    amp_gonzales   strdis  strdiscretized_shifted_levels_1_and_2_encoding   
2    amp_gonzales   strbin       strbinary_shifted_levels_1_and_2_encoding   
3    amp_gonzales   seqbin       seqbinary_shifted_levels_1_and_2_encoding   
4      amp_iamp2l   strbin       strbinary_shifted_levels_1_and_2_encoding   
..            ...      ...                                             ...   
111     cpp_mixed   strbin       strbinary_shifted_levels_1_and_2_encoding   
112   cpp_sanders   strdis  strdiscretized_shifted_levels_1_and_2_encoding   
113   cpp_sanders   seqdis  seqdiscretized_shifted_levels_1_and_2_encoding   
114   cpp_sanders   strbin       strbinary_shifted_levels_1_and_2_encoding   
115   cpp_sanders   seqbin       seqbinary_shifted_levels_1_and_2_encoding   

           F1            type  is_imbalanced bio_field  type_field  missing  
0    0.571429  sequence based       0.209302       amp           1    False  
1    0.571429  sequence based       0.209302       amp           1    False  
2    0.500000  sequence based       0.209302       amp           1    False  
3    0.500000  sequence based       0.209302       amp           1    False  
4    0.708928  sequence based       0.267661       amp           1    False  
..        ...             ...            ...       ...         ...      ...  
111  0.863636  sequence based       0.757812       cpp           1    False  
112  0.862745  sequence based       0.765517       cpp           1    False  
113  0.862745  sequence based       0.765517       cpp           1    False  
114  0.862745  sequence based       0.765517       cpp           1    False  
115  0.862745  sequence based       0.765517       cpp           1    False  

[116 rows x 9 columns]

In [8]:
df_cmangoes_source_data = df_clean_cmangoes_data(df_cmangoes_source_data)
df_cmangoes_imb_data = df_clean_cmangoes_data(df_cmangoes_imb_data)
df_cmangoes_bio_data = df_clean_cmangoes_data(df_cmangoes_bio_data)

df_cmangoes_source_data

Dataset       Encoding                      Encoding_max        F1  \
0     amp_gonzales  param_seq_dis  CMANGOES_seq_discretized_shifted  0.571429   
1     amp_gonzales  param_seq_bin       CMANGOES_seq_binary_shifted  0.500000   
2       amp_iamp2l  param_seq_dis  CMANGOES_seq_discretized_shifted  0.716014   
3       amp_iamp2l  param_seq_bin       CMANGOES_seq_binary_shifted  0.708928   
4        acp_mlacp  param_seq_dis  CMANGOES_seq_discretized_shifted  0.403390   
5        acp_mlacp  param_seq_bin       CMANGOES_seq_binary_shifted  0.353913   
6        cpp_mlcpp  param_seq_dis  CMANGOES_seq_discretized_shifted  0.401970   
7        cpp_mlcpp  param_seq_bin       CMANGOES_seq_binary_shifted  0.379744   
8      aip_aippred  param_seq_bin       CMANGOES_seq_binary_shifted  0.476557   
9      aip_aippred  param_seq_dis  CMANGOES_seq_discretized_shifted  0.483782   
10        acp_iacp  param_seq_bin       CMANGOES_seq_binary_shifted  0.352941   
11        acp_iacp  param_seq_dis  CMANGOES_seq_discretized_shifted  0.410256   
12  aip_antiinflam  param_seq_bin       CMANGOES_seq_binary_shifted  0.444450   
13  aip_antiinflam  param_seq_dis  CMANGOES_seq_discretized_shifted  0.470537   
14    ace_vaxinpad  param_seq_dis  CMANGOES_seq_discretized_shifted  0.618182   
15    ace_vaxinpad  param_seq_bin       CMANGOES_seq_binary_shifted  0.609477   
16        bce_ibce  param_seq_dis  CMANGOES_seq_discretized_shifted  0.516849   
17        bce_ibce  param_seq_bin       CMANGOES_seq_binary_shifted  0.505379   
18      hem_hemopi  param_seq_dis  CMANGOES_seq_discretized_shifted  0.696085   
19      hem_hemopi  param_seq_bin       CMANGOES_seq_binary_shifted  0.668309   
20     amp_modlamp  param_seq_dis  CMANGOES_seq_discretized_shifted  0.768068   
21     amp_modlamp  param_seq_bin       CMANGOES_seq_binary_shifted  0.725397   
22   amp_fernandes  param_seq_dis  CMANGOES_seq_discretized_shifted  0.696939   
23   amp_fernandes  param_seq_bin       CMANGOES_seq_binary_shifted  0.694765   
24     cpp_cellppd  param_seq_bin       CMANGOES_seq_binary_shifted  0.679138   
25    cpp_cppredfl  param_seq_bin       CMANGOES_seq_binary_shifted  0.564254   
26     avp_amppred  param_seq_bin       CMANGOES_seq_binary_shifted  0.638235   
27     atb_iantitb  param_seq_bin       CMANGOES_seq_binary_shifted  0.604639   
28       amp_csamp  param_seq_dis  CMANGOES_seq_discretized_shifted  0.925926   
29     afp_amppred  param_seq_dis  CMANGOES_seq_discretized_shifted  0.667239   
30     atb_antitbp  param_seq_dis  CMANGOES_seq_discretized_shifted  0.595999   
31     atb_iantitb  param_seq_dis  CMANGOES_seq_discretized_shifted  0.613237   
32     avp_amppred  param_seq_dis  CMANGOES_seq_discretized_shifted  0.649503   
33      acp_anticp  param_seq_dis  CMANGOES_seq_discretized_shifted  0.715789   
34     cpp_cellppd  param_seq_dis  CMANGOES_seq_discretized_shifted  0.690515   
35    cpp_cppredfl  param_seq_dis  CMANGOES_seq_discretized_shifted  0.545455   
36       amp_csamp  param_seq_bin       CMANGOES_seq_binary_shifted  0.928571   
37     cpp_mlcppue  param_seq_dis  CMANGOES_seq_discretized_shifted  0.619381   
38     afp_amppred  param_seq_bin       CMANGOES_seq_binary_shifted  0.656542   
39     cpp_mlcppue  param_seq_bin       CMANGOES_seq_binary_shifted  0.601205   
40      acp_anticp  param_seq_bin       CMANGOES_seq_binary_shifted  0.708374   
41     atb_antitbp  param_seq_bin       CMANGOES_seq_binary_shifted  0.593706   
42      afp_antifp  param_seq_bin       CMANGOES_seq_binary_shifted  0.536668   
43      afp_antifp  param_seq_dis  CMANGOES_seq_discretized_shifted  0.554842   
44      amp_antibp  param_seq_dis  CMANGOES_seq_discretized_shifted  0.695652   
45      amp_antibp  param_seq_bin       CMANGOES_seq_binary_shifted  0.670888   
46  cpp_cellppdmod  param_seq_bin       CMANGOES_seq_binary_shifted  0.745315   
47  cpp_cellppdmod  param_seq_dis  CMANGOES_seq_discretized_shifted  0.754583   
48     amp_antibp2  param_seq_dis  CMANGOE

In [9]:
df_peptidereactor_source_data

Dataset Encoding                                    Encoding_max  \
0    amp_gonzales   seqdis  seqdiscretized_shifted_levels_1_and_2_encoding   
1    amp_gonzales   strdis  strdiscretized_shifted_levels_1_and_2_encoding   
2    amp_gonzales   strbin       strbinary_shifted_levels_1_and_2_encoding   
3    amp_gonzales   seqbin       seqbinary_shifted_levels_1_and_2_encoding   
4      amp_iamp2l   strbin       strbinary_shifted_levels_1_and_2_encoding   
..            ...      ...                                             ...   
111     cpp_mixed   strbin       strbinary_shifted_levels_1_and_2_encoding   
112   cpp_sanders   strdis  strdiscretized_shifted_levels_1_and_2_encoding   
113   cpp_sanders   seqdis  seqdiscretized_shifted_levels_1_and_2_encoding   
114   cpp_sanders   strbin       strbinary_shifted_levels_1_and_2_encoding   
115   cpp_sanders   seqbin       seqbinary_shifted_levels_1_and_2_encoding   

           F1            type  is_imbalanced bio_field  type_field  missing  
0    0.571429  sequence based       0.209302       amp           1    False  
1    0.571429  sequence based       0.209302       amp           1    False  
2    0.500000  sequence based       0.209302       amp           1    False  
3    0.500000  sequence based       0.209302       amp           1    False  
4    0.708928  sequence based       0.267661       amp           1    False  
..        ...             ...            ...       ...         ...      ...  
111  0.863636  sequence based       0.757812       cpp           1    False  
112  0.862745  sequence based       0.765517       cpp           1    False  
113  0.862745  sequence based       0.765517       cpp           1    False  
114  0.862745  sequence based       0.765517       cpp           1    False  
115  0.862745  sequence based       0.765517       cpp           1    False  

[116 rows x 9 columns]

In [10]:
df_combined_source_data = pd.concat(
    [df_cmangoes_source_data, df_peptidereactor_source_data],
    ignore_index=True)
df_combined_imb_data = pd.concat(
    [df_cmangoes_imb_data, df_peptidereactor_imb_data], ignore_index=True)
df_combined_bio_data = pd.concat(
    [df_cmangoes_bio_data, df_peptidereactor_bio_data], ignore_index=True)

df_combined_source_data

Dataset       Encoding  \
0    amp_gonzales  param_seq_dis   
1    amp_gonzales  param_seq_bin   
2      amp_iamp2l  param_seq_dis   
3      amp_iamp2l  param_seq_bin   
4       acp_mlacp  param_seq_dis   
..            ...            ...   
169     cpp_mixed         strbin   
170   cpp_sanders         strdis   
171   cpp_sanders         seqdis   
172   cpp_sanders         strbin   
173   cpp_sanders         seqbin   

                                       Encoding_max        F1            type  \
0                  CMANGOES_seq_discretized_shifted  0.571429  sequence based   
1                       CMANGOES_seq_binary_shifted  0.500000  sequence based   
2                  CMANGOES_seq_discretized_shifted  0.716014  sequence based   
3                       CMANGOES_seq_binary_shifted  0.708928  sequence based   
4                  CMANGOES_seq_discretized_shifted  0.403390  sequence based   
..                                              ...       ...             ...   
169       strbinary_shifted_levels_1_and_2_encoding  0.863636  sequence based   
170  strdiscretized_shifted_levels_1_and_2_encoding  0.862745  sequence based   
171  seqdiscretized_shifted_levels_1_and_2_encoding  0.862745  sequence based   
172       strbinary_shifted_levels_1_and_2_encoding  0.862745  sequence based   
173       seqbinary_shifted_levels_1_and_2_encoding  0.862745  sequence based   

     is_imbalanced bio_field  type_field  missing  
0         0.209302       amp           1    False  
1         0.209302       amp           1    False  
2         0.267661       amp           1    False  
3         0.267661       amp           1    False  
4         0.319658       acp           1    False  
..             ...       ...         ...      ...  
169       0.757812       cpp           1    False  
170       0.765517       cpp           1    False  
171       0.765517       cpp           1    False  
172       0.765517       cpp           1    False  
173       0.765517       cpp           1    False  

[174 rows x 9 columns]

In [11]:
df_combined_source_data

Dataset       Encoding  \
0    amp_gonzales  param_seq_dis   
1    amp_gonzales  param_seq_bin   
2      amp_iamp2l  param_seq_dis   
3      amp_iamp2l  param_seq_bin   
4       acp_mlacp  param_seq_dis   
..            ...            ...   
169     cpp_mixed         strbin   
170   cpp_sanders         strdis   
171   cpp_sanders         seqdis   
172   cpp_sanders         strbin   
173   cpp_sanders         seqbin   

                                       Encoding_max        F1            type  \
0                  CMANGOES_seq_discretized_shifted  0.571429  sequence based   
1                       CMANGOES_seq_binary_shifted  0.500000  sequence based   
2                  CMANGOES_seq_discretized_shifted  0.716014  sequence based   
3                       CMANGOES_seq_binary_shifted  0.708928  sequence based   
4                  CMANGOES_seq_discretized_shifted  0.403390  sequence based   
..                                              ...       ...             ...   
169       strbinary_shifted_levels_1_and_2_encoding  0.863636  sequence based   
170  strdiscretized_shifted_levels_1_and_2_encoding  0.862745  sequence based   
171  seqdiscretized_shifted_levels_1_and_2_encoding  0.862745  sequence based   
172       strbinary_shifted_levels_1_and_2_encoding  0.862745  sequence based   
173       seqbinary_shifted_levels_1_and_2_encoding  0.862745  sequence based   

     is_imbalanced bio_field  type_field  missing  
0         0.209302       amp           1    False  
1         0.209302       amp           1    False  
2         0.267661       amp           1    False  
3         0.267661       amp           1    False  
4         0.319658       acp           1    False  
..             ...       ...         ...      ...  
169       0.757812       cpp           1    False  
170       0.765517       cpp           1    False  
171       0.765517       cpp           1    False  
172       0.765517       cpp           1    False  
173       0.765517       cpp           1    False  

[174 rows x 9 columns]

In [12]:
# Add one more column to flag missing values
df_combined_source_data['Value'] = [
    'NaN' if i is True else 'notNaN'
    for i in df_combined_source_data['F1'].isnull().tolist()]
df_combined_imb_data['Value'] = [
    'NaN' if i is True else 'notNaN'
    for i in df_combined_imb_data['F1'].isnull().tolist()]
df_combined_bio_data['Value'] = [
    'NaN' if i is True else 'notNaN'
    for i in df_combined_bio_data['F1'].isnull().tolist()]

In [13]:
df_combined_source_data

Dataset       Encoding  \
0    amp_gonzales  param_seq_dis   
1    amp_gonzales  param_seq_bin   
2      amp_iamp2l  param_seq_dis   
3      amp_iamp2l  param_seq_bin   
4       acp_mlacp  param_seq_dis   
..            ...            ...   
169     cpp_mixed         strbin   
170   cpp_sanders         strdis   
171   cpp_sanders         seqdis   
172   cpp_sanders         strbin   
173   cpp_sanders         seqbin   

                                       Encoding_max        F1            type  \
0                  CMANGOES_seq_discretized_shifted  0.571429  sequence based   
1                       CMANGOES_seq_binary_shifted  0.500000  sequence based   
2                  CMANGOES_seq_discretized_shifted  0.716014  sequence based   
3                       CMANGOES_seq_binary_shifted  0.708928  sequence based   
4                  CMANGOES_seq_discretized_shifted  0.403390  sequence based   
..                                              ...       ...             ...   
169       strbinary_shifted_levels_1_and_2_encoding  0.863636  sequence based   
170  strdiscretized_shifted_levels_1_and_2_encoding  0.862745  sequence based   
171  seqdiscretized_shifted_levels_1_and_2_encoding  0.862745  sequence based   
172       strbinary_shifted_levels_1_and_2_encoding  0.862745  sequence based   
173       seqbinary_shifted_levels_1_and_2_encoding  0.862745  sequence based   

     is_imbalanced bio_field  type_field  missing   Value  
0         0.209302       amp           1    False  notNaN  
1         0.209302       amp           1    False  notNaN  
2         0.267661       amp           1    False  notNaN  
3         0.267661       amp           1    False  notNaN  
4         0.319658       acp           1    False  notNaN  
..             ...       ...         ...      ...     ...  
169       0.757812       cpp           1    False  notNaN  
170       0.765517       cpp           1    False  notNaN  
171       0.765517       cpp           1    False  notNaN  
172       0.765517       cpp           1    False  notNaN  
173       0.765517       cpp           1    False  notNaN  

[174 rows x 10 columns]

In [14]:
# We want to drop rows that contain 'zzz' at the end of the necoding
# This flags were used to seperate heatmap
df_combined_source_data.drop(
    df_combined_source_data[
        df_combined_source_data['Encoding'].str.endswith('zzz')].index,
    inplace=True)
df_combined_imb_data.drop(
    df_combined_imb_data[
        df_combined_imb_data['Encoding'].str.endswith('zzz')].index,
    inplace=True)
df_combined_bio_data.drop(
    df_combined_bio_data[
        df_combined_bio_data['Encoding'].str.endswith('zzz')].index,
    inplace=True)

df_combined_source_data

Dataset       Encoding  \
0    amp_gonzales  param_seq_dis   
1    amp_gonzales  param_seq_bin   
2      amp_iamp2l  param_seq_dis   
3      amp_iamp2l  param_seq_bin   
4       acp_mlacp  param_seq_dis   
..            ...            ...   
169     cpp_mixed         strbin   
170   cpp_sanders         strdis   
171   cpp_sanders         seqdis   
172   cpp_sanders         strbin   
173   cpp_sanders         seqbin   

                                       Encoding_max        F1            type  \
0                  CMANGOES_seq_discretized_shifted  0.571429  sequence based   
1                       CMANGOES_seq_binary_shifted  0.500000  sequence based   
2                  CMANGOES_seq_discretized_shifted  0.716014  sequence based   
3                       CMANGOES_seq_binary_shifted  0.708928  sequence based   
4                  CMANGOES_seq_discretized_shifted  0.403390  sequence based   
..                                              ...       ...             ...   
169       strbinary_shifted_levels_1_and_2_encoding  0.863636  sequence based   
170  strdiscretized_shifted_levels_1_and_2_encoding  0.862745  sequence based   
171  seqdiscretized_shifted_levels_1_and_2_encoding  0.862745  sequence based   
172       strbinary_shifted_levels_1_and_2_encoding  0.862745  sequence based   
173       seqbinary_shifted_levels_1_and_2_encoding  0.862745  sequence based   

     is_imbalanced bio_field  type_field  missing   Value  
0         0.209302       amp           1    False  notNaN  
1         0.209302       amp           1    False  notNaN  
2         0.267661       amp           1    False  notNaN  
3         0.267661       amp           1    False  notNaN  
4         0.319658       acp           1    False  notNaN  
..             ...       ...         ...      ...     ...  
169       0.757812       cpp           1    False  notNaN  
170       0.765517       cpp           1    False  notNaN  
171       0.765517       cpp           1    False  notNaN  
172       0.765517       cpp           1    False  notNaN  
173       0.765517       cpp           1    False  notNaN  

[174 rows x 10 columns]

# 3. Visualize
## 3.1. CMANGOES results

In [17]:
def chart_visualize(df_input, string_title, flag_cmangoes_style):
    
    if flag_cmangoes_style:
        scale_general = alt.Scale(scheme='greys')
        scale_na_values = alt.Scale(domain=['NaN'], range=['#CD7DA9'])
    else:
        scale_general = alt.Scale(range=["#a6bddb", "#023858"])
        scale_na_values = alt.Scale(domain=['NaN'], range=['#a6611a'])
    
    
    chart_non_null = alt.Chart(
        df_input, title=string_title + " multi-dataset results"
    ).mark_rect().encode(
        x=alt.X('Encoding', type='nominal', axis=alt.Axis(labelAngle=-45)),
        y=alt.Y('Dataset', type='nominal',
                scale=alt.Scale(domain=list_of_datasets)),
        color=alt.Color('F1', type='quantitative', scale=scale_general),
        tooltip=['Dataset', 'Encoding_max', 'F1', 'is_imbalanced', 'bio_field']
    )
    
    chart_null = alt.Chart(
        df_input, title=string_title + " multi-dataset results"
    ).mark_rect().encode(
        x=alt.X('Encoding', type='nominal', axis=alt.Axis(labelAngle=-45)),
        y=alt.Y('Dataset', type='nominal',
                scale=alt.Scale(domain=list_of_datasets)),
        color=alt.Color('Value', type='nominal', scale=scale_na_values),
        tooltip=['Dataset', 'Encoding_max', 'F1', 'is_imbalanced', 'bio_field']
    )
    
    chart_result = chart_non_null + chart_null
    
    return chart_result


def replicate_visualizations(flag_visualization_style):
    chart_cmangoes_source_result = chart_visualize(
        df_cmangoes_source_data, 'CMANGOES source', flag_visualization_style)
    chart_peptidereactor_source_result = chart_visualize(
        df_peptidereactor_source_data, 'Peptidereactor source',
        flag_visualization_style)
    chart_peptidereactor_imb_result = chart_visualize(
        df_peptidereactor_imb_data, 'Peptidereactor imb',
        flag_visualization_style)
    chart_peptidereactor_bio_result = chart_visualize(
        df_peptidereactor_bio_data, 'Peptidereactor bio',
        flag_visualization_style)
    chart_combined_source_result = chart_visualize(
        df_combined_source_data, 'Combined source', flag_visualization_style)
    chart_combined_imb_result = chart_visualize(
        df_combined_imb_data, 'Combined imb', flag_visualization_style)
    chart_combined_bio_result = chart_visualize(
        df_combined_bio_data, 'Combined bio', flag_visualization_style)

    chart_result = chart_cmangoes_source_result &\
                   chart_peptidereactor_imb_result &\
                   chart_peptidereactor_bio_result &\
                   chart_combined_imb_result &\
                   chart_combined_bio_result
    
    
    return chart_result


def filter_and_visualize_datasets():
    
    #.transform_filter(
    #    alt.FieldEqualPredicate(field='year', equal=2000)
    #)
    # https://altair-viz.github.io/user_guide/transform/filter.html
    
    return None


## 3.1. Peptidereactor-styled results

In [18]:
flag_cmangoes_style = True
replicate_visualizations(not flag_cmangoes_style)

alt.VConcatChart(...)

## 3.2. Our own visualizations

In [19]:
replicate_visualizations(flag_cmangoes_style)

alt.VConcatChart(...)

## 3.3 Further analysis

SyntaxError: invalid syntax (761895771.py, line 1)